<a href="https://colab.research.google.com/github/rrnM12/git_test/blob/main/EEG_DistilBERT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
!pip install mne

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 79.7 MB/s eta 0:00:00


In [ ]:
!pip install transformers

Looking in indexes: https://pypi.org/simple, https://us-python.pkg.dev/colab-wheels/public/simple/
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.3/6.3 MB 77.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 190.3/190.3 KB 12.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.6/7.6 MB 22.6 MB/s eta 0:00:00


In [ ]:
# import necessary libraries
import numpy as np
import pandas as pd
import csv
import pickle
import mne
import matplotlib.pyplot as plt
from tqdm import tqdm
import torch
np.random.seed(42)
torch.manual_seed(42)

In [ ]:
# load in EEG dataset
raw = mne.io.read_raw_brainvision(r"/content/drive/MyDrive/EEG_project/benign_EEG/Brainvision_datasets/ds003825-download/sub-01/eeg/sub-01_task-rsvp_eeg.vhdr")


Extracting parameters from /content/drive/MyDrive/EEG_project/benign_EEG/Brainvision_datasets/ds003825-download/sub-01/eeg/sub-01_task-rsvp_eeg.vhdr...
Setting channel info structure...


In [ ]:
# Transformer

# pretend 1 and 2 have alzheimers by creating own y train and y test
# create transformer
# train transformer
# check reults

# import python packages
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd

In [ ]:
# creating distilBERT
"""
import transformers
import torch
from transformers import DistilBertConfig, DistilBertForSequenceClassification
from transformers import AutoModelForSequenceClassification
from transformers import AutoModel

model = AutoModelForSequenceClassification.from_pretrained("distilbert-base-uncased", num_labels=1)
"""

'\nimport transformers\nimport torch\nfrom transformers import DistilBertConfig, DistilBertForSequenceClassification\nfrom transformers import AutoModelForSequenceClassification\nfrom transformers import AutoModel\n\nmodel = AutoModelForSequenceClassification.from_pretrained("distilbert-base-uncased", num_labels=1)\n'

In [ ]:
a = torch.zeros(1,512)
a[0][0]=1

In [ ]:
import transformers
from transformers import DistilBertConfig, DistilBertModel

# Initializing a DistilBERT configuration
configuration = DistilBertConfig()

# Initializing a model (with random weights) from the configuration
model = DistilBertModel(configuration)

import torch.nn as nn
from transformers import AutoModel
class PosModel(nn.Module):
    def __init__(self):
        super(PosModel, self).__init__()

        # Initializing a DistilBERT configuration
        self.configuration = DistilBertConfig()

        # Initializing a model (with random weights) from the configuration
        model = DistilBertModel(configuration)

        self.base_model = model
        self.dropout = nn.Dropout(0)
        self.linear = nn.Linear(768, 1) # output features from bert is 768 and 2 is ur number of labels

    def forward(self, embeds):

        outputs = self.base_model.transformer.forward(
                                        embeds,
                                        attn_mask= a.to('cuda'),
                                        head_mask=[None]*self.configuration.num_hidden_layers)

        # You write you new head here
        # print(outputs)
        # print(outputs.keys())
        outputs = self.dropout(outputs[0])
        outputs = self.linear(outputs) # outputs.last_hidden_state

        return outputs

model = PosModel()
model.to('cuda')

PosModel(
  (base_model): DistilBertModel(
    (embeddings): Embeddings(
      (word_embeddings): Embedding(30522, 768, padding_idx=0)
      (position_embeddings): Embedding(512, 768)
      (LayerNorm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
      (dropout): Dropout(p=0.1, inplace=False)
    )
    (transformer): Transformer(
      (layer): ModuleList(
        (0): TransformerBlock(
          (attention): MultiHeadSelfAttention(
            (dropout): Dropout(p=0.1, inplace=False)
            (q_lin): Linear(in_features=768, out_features=768, bias=True)
            (k_lin): Linear(in_features=768, out_features=768, bias=True)
            (v_lin): Linear(in_features=768, out_features=768, bias=True)
            (out_lin): Linear(in_features=768, out_features=768, bias=True)
          )
          (sa_layer_norm): LayerNorm((768,), eps=1e-12, elementwise_affine=True)
          (ffn): FFN(
            (dropout): Dropout(p=0.1, inplace=False)
            (lin1): Linear(in_feat

In [ ]:
# attributes of the model
# print(config)

In [ ]:
# used to create X_train and y_train

import numpy as np
import torch
from transformers import AutoTokenizer, AutoModel


def get_word_idx(sent: str, word: str):
    return sent.split(" ").index(word)


def get_hidden_states(encoded, token_ids_word, model, layers):
    """Push input IDs through model. Stack and sum `layers` (last four by default).
    Select only those subword token outputs that belong to our word of interest
    and average them."""
    with torch.no_grad():
        output = model(**encoded)

    # Get all hidden states
    states = output.hidden_states
    # Stack and sum all requested layers
    output = torch.stack([states[i] for i in layers]).sum(0).squeeze()
    # Only select the tokens that constitute the requested word
    word_tokens_output = output[token_ids_word]

    return word_tokens_output.mean(dim=0)


def get_word_vector(sent, idx, tokenizer, model, layers):
    """Get a word vector by first tokenizing the input sentence, getting all token idxs
    that make up the word of interest, and then `get_hidden_states`."""

    # gives token id's
    encoded = tokenizer.encode_plus(sent, return_tensors="pt")
    # get all token idxs that belong to the word of interest
    token_ids_word = np.where(np.array(encoded.word_ids()) == idx)

    return get_hidden_states(encoded, token_ids_word, model, layers)


def main(layers=None):
    # Use last four layers by default
    layers = [-4, -3, -2, -1] if layers is None else layers

    # tokenizer from specific model
    tokenizer = AutoTokenizer.from_pretrained("bert-base-cased")

    # want to see output of each hidden layer (returns the model)
    model = AutoModel.from_pretrained("bert-base-cased", output_hidden_states=True)

    sent = "I like cookies ."

    # splits the sentence into list of words and find index of specific word
    idx = get_word_idx(sent, "cookies")

    word_embedding = get_word_vector(sent, idx, tokenizer, model, layers)

    return word_embedding


if __name__ == '__main__':
    main()

# this is x train of KNN

Some weights of the model checkpoint at bert-base-cased were not used when initializing BertModel: ['cls.predictions.transform.LayerNorm.weight', 'cls.predictions.transform.dense.weight', 'cls.seq_relationship.weight', 'cls.predictions.decoder.weight', 'cls.predictions.transform.LayerNorm.bias', 'cls.predictions.transform.dense.bias', 'cls.seq_relationship.bias', 'cls.predictions.bias']
- This IS expected if you are initializing BertModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing BertModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).


In [ ]:
# import necessary libraries
import numpy as np
import pandas as pd
import csv
import pickle
import mne
import matplotlib.pyplot as plt

In [ ]:
# loading in dictionary

f = open('/content/drive/MyDrive/EEG_project/dictionary_of_words.txt')
content = f.read()
dictionary = content.split()

In [ ]:
word_token_IDs = torch.load('/content/drive/MyDrive/EEG_project/Code/DistilBERT/word_token_IDs_DistilBERT.pt')

In [ ]:
word_embedding = torch.load('/content/drive/MyDrive/EEG_project/Code/DistilBERT/word_embedding_DistilBERT.pt')

In [ ]:
word_embedding = torch.stack(word_embedding)
word_embedding = torch.reshape(word_embedding, (-1,768))

In [ ]:
original_word_token_IDs = word_token_IDs

In [ ]:
word_embedding

tensor([[ 0.2232, -0.0728, -0.1760,  ...,  0.3025,  0.3452,  0.0871],
        [ 0.0848, -0.2423, -0.1013,  ...,  0.2219,  0.4752,  0.0991],
        [ 0.3137, -0.0232, -0.2380,  ...,  0.3390,  0.2818,  0.2789],
        ...,
        [ 0.1690, -0.0031, -0.3363,  ..., -0.0099,  0.1580,  0.0606],
        [ 0.2127, -0.0228, -0.0986,  ...,  0.2259,  0.4397,  0.2094],
        [ 0.3644,  0.1625, -0.1243,  ..., -0.1045,  0.2717,  0.1279]])

In [ ]:
# word_embedding = word_embedding.numpy()
type(word_embedding)

torch.Tensor

In [ ]:
# create attention masks and work token IDs

attention_masks = []
word_token_IDs = []


for i in range(len(original_word_token_IDs)):
  attention_masks.append(original_word_token_IDs[i]['attention_mask'])
  word_token_IDs.append(original_word_token_IDs[i]['input_ids'])

In [ ]:
new = []
for i in range(len(attention_masks)):
  for j in range(len(attention_masks[i])):
    new.append(attention_masks[i][j])

attention_masks = new


new = []
for i in range(len(word_token_IDs)):
  for j in range(len(word_token_IDs[i])):
    new.append(word_token_IDs[i][j])

word_token_IDs = new

In [ ]:
word_token_IDs

[tensor([ 101,  170, 1161,  102,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,    0,
            0,    0,    0,  

In [ ]:
new = []
for i in range(len(attention_masks)):
  new.append([])
  for j in range(len(attention_masks[i])):
    x = attention_masks[i][j].item()
    new[i].append(x)

attention_masks = new

new = []
for i in range(len(word_token_IDs)):
  new.append([])
  for j in range(len(word_token_IDs[i])):
    x = word_token_IDs[i][j].item()
    new[i].append(x)

word_token_IDs = new

In [ ]:
# checking both look good

# attention_masks = np.array(attention_masks)
# word_token_IDs = np.array(word_token_IDs)

In [ ]:
# cleaning y train by removing all zeros and first and last value in each list
# convert each one to tuple
# y_train = [(170,1161), (234155,467), ... , (11092), ...]

longest = 0
new_word_token_IDs = []

for i in range(len(word_token_IDs)):
    temp = [value for value in word_token_IDs[i] if value != 0]
    del temp[0]
    del temp[-1]
    if (len(temp) > longest):
        longest = len(temp)
    new_word_token_IDs.append(temp)


    # pad word_token_ids
longest

7

In [ ]:
word_token_IDs = new_word_token_IDs
print(word_token_IDs)

[[170, 1161], [170, 2881, 8997, 1377], [170, 1813, 5084], [170, 4197], [170, 2822, 6697], [11092], [3928], [22634], [25356], [11092, 1116], [170, 27261], [14049], [19966], [19966, 1116], [14701], [24716], [170, 1830, 13890], [22586], [170, 1830, 13890, 1158], [170, 1830, 11243], [170, 1830, 11243, 1116], [170, 3169, 6108], [170, 16632, 1906], [170, 22742], [170, 14598, 1158], [170, 5567, 21347, 1233], [7134], [2912], [170, 18075, 3171], [1682], [22832], [22832, 4233], [22832, 1785], [22832, 1193], [7161], [170, 4043, 2007], [170, 15792, 2944], [170, 4043, 14503, 2165], [170, 4043, 9204], [170, 12207, 24874, 7050], [170, 12207, 1204], [12030], [12030, 1116], [170, 8346], [1164], [1807], [1807, 4015], [170, 6766, 8788], [170, 9730, 12788], [6629], [20494], [9354], [170, 4832], [170, 4832, 7235, 4902], [5884], [5884, 1116], [10040], [10040, 3051], [7846], [7284], [7846, 1116], [170, 4832, 4063, 12964], [170, 4832, 4063, 5790], [18055], [8761], [18055, 3452], [23774], [18099], [170, 4832, 

In [ ]:
for i in range(len(word_token_IDs)):
    for j in range(longest-len(word_token_IDs[i])):
        word_token_IDs[i].append(0)


word_token_IDs

[[170, 1161, 0, 0, 0, 0, 0],
 [170, 2881, 8997, 1377, 0, 0, 0],
 [170, 1813, 5084, 0, 0, 0, 0],
 [170, 4197, 0, 0, 0, 0, 0],
 [170, 2822, 6697, 0, 0, 0, 0],
 [11092, 0, 0, 0, 0, 0, 0],
 [3928, 0, 0, 0, 0, 0, 0],
 [22634, 0, 0, 0, 0, 0, 0],
 [25356, 0, 0, 0, 0, 0, 0],
 [11092, 1116, 0, 0, 0, 0, 0],
 [170, 27261, 0, 0, 0, 0, 0],
 [14049, 0, 0, 0, 0, 0, 0],
 [19966, 0, 0, 0, 0, 0, 0],
 [19966, 1116, 0, 0, 0, 0, 0],
 [14701, 0, 0, 0, 0, 0, 0],
 [24716, 0, 0, 0, 0, 0, 0],
 [170, 1830, 13890, 0, 0, 0, 0],
 [22586, 0, 0, 0, 0, 0, 0],
 [170, 1830, 13890, 1158, 0, 0, 0],
 [170, 1830, 11243, 0, 0, 0, 0],
 [170, 1830, 11243, 1116, 0, 0, 0],
 [170, 3169, 6108, 0, 0, 0, 0],
 [170, 16632, 1906, 0, 0, 0, 0],
 [170, 22742, 0, 0, 0, 0, 0],
 [170, 14598, 1158, 0, 0, 0, 0],
 [170, 5567, 21347, 1233, 0, 0, 0],
 [7134, 0, 0, 0, 0, 0, 0],
 [2912, 0, 0, 0, 0, 0, 0],
 [170, 18075, 3171, 0, 0, 0, 0],
 [1682, 0, 0, 0, 0, 0, 0],
 [22832, 0, 0, 0, 0, 0, 0],
 [22832, 4233, 0, 0, 0, 0, 0],
 [22832, 1785, 0, 0, 0, 0

In [ ]:
# is this correct
IDs = np.arange(len(word_embedding))

IDs

array([    0,     1,     2, ..., 25319, 25320, 25321])

In [ ]:
def z_norm(table):
  table=table.T# need to transpose it since the functions work like that
  sd=np.std(table)
  mean=np.mean(table)
  numerator=table-mean #numerator in the formula for z-score
  z_score=numerator/sd
  z_norm_table=z_score.T #we transpose again and we have the initial table but with all the
  #values z-scored by row.
  return z_norm_table

In [ ]:
from sklearn import preprocessing

word_embedding = np.array(word_embedding)

word_embedding = preprocessing.normalize(word_embedding)

# word_embedding = preprocessing.normalize(word_embedding)
print(type(word_embedding))

# for i in range(len(word_embedding)):
    # print(word_embedding[i].shape)

print(word_embedding)

<class 'numpy.ndarray'>
[[ 0.02049945 -0.00668782 -0.01616044 ...  0.0277793   0.03170164
   0.0080008 ]
 [ 0.00780691 -0.02229709 -0.00932162 ...  0.02042081  0.04373314
   0.0091171 ]
 [ 0.02809204 -0.00208188 -0.02131671 ...  0.03036119  0.02523983
   0.02497477]
 ...
 [ 0.01488235 -0.0002741  -0.02961088 ... -0.00087609  0.01391527
   0.00533901]
 [ 0.01975627 -0.0021211  -0.00916077 ...  0.02098848  0.04084845
   0.01945864]
 [ 0.03350511  0.01493698 -0.01143299 ... -0.00961115  0.02498538
   0.01176387]]


In [ ]:

word_embedding[0]

array([ 2.04994548e-02, -6.68782461e-03, -1.61604397e-02,  3.38339549e-03,
       -8.61363392e-03,  3.72272287e-03,  2.13203579e-02, -7.47115863e-03,
        1.45110162e-02, -1.92864127e-02,  3.83171748e-04,  3.42250690e-02,
       -2.76581328e-02, -3.29035856e-02, -3.33275460e-02, -9.43955034e-04,
       -1.79252420e-02,  1.65934172e-02,  1.16591109e-02,  1.63902082e-02,
       -3.01889353e-03, -2.16204859e-02,  4.45380760e-03, -1.25036901e-02,
       -1.63377225e-02, -1.45066278e-02,  1.07928086e-02,  2.09459830e-02,
       -1.90311857e-02,  2.88191922e-02,  1.08347246e-02,  9.04698949e-03,
        1.73809882e-02,  6.69287925e-04, -3.96832190e-02, -1.30957756e-02,
        2.60776319e-02,  2.32108422e-02, -1.56207271e-02,  1.03117218e-02,
       -1.63934734e-02, -1.17253819e-02, -8.87117814e-04,  7.24232942e-03,
       -1.49535183e-02,  1.78247429e-02, -2.67324634e-02, -4.75011207e-03,
       -3.10911126e-02,  2.93511525e-02, -3.18189641e-03, -3.93373109e-02,
       -3.81659344e-03,  

In [ ]:
# train knn with sk learn
from sklearn.neighbors import KNeighborsClassifier

classifier = KNeighborsClassifier(n_neighbors = 1)
classifier.fit(word_embedding, IDs)

KNeighborsClassifier(n_neighbors=1)

In [ ]:
# normalize both inputs (word_embeddings and EEG)
# create reverse mapping from IDs to word_token_IDs
# feed into Distilbert
# think about how to deal with different EEG channels
# get notebooks ready

In [ ]:
from sklearn.metrics import accuracy_score

pred = classifier.predict(word_embedding)
print(accuracy_score(IDs, pred))

1.0


In [ ]:
# creating distilBERT
"""
import transformers
import torch
from transformers import DistilBertConfig, DistilBertModel

from transformers import AutoModelForSequenceClassification

model = AutoModelForSequenceClassification.from_pretrained("distilbert-base-uncased", num_labels=1) # changed one to two
"""

"""
# Initializing a DistilBERT configuration
config = DistilBertConfig()

# Initializing a model (with random weights) from the configuration
model = DistilBertModel(config)

# Accessing the model configuration
config = model.config
"""

'\n# Initializing a DistilBERT configuration\nconfig = DistilBertConfig()\n\n# Initializing a model (with random weights) from the configuration\nmodel = DistilBertModel(config)\n\n# Accessing the model configuration\nconfig = model.config\n'

In [ ]:
from torch.optim import AdamW

optimizer = AdamW(model.parameters(), lr=5e-25) # 1e-4, 1e-3, 1e-2

In [ ]:
from transformers import get_scheduler

num_training_steps = 684 #684*epochs
lr_scheduler = transformers.get_scheduler(
    name="linear", optimizer=optimizer, num_warmup_steps=0, num_training_steps=num_training_steps)       # num_training_steps=num_training_steps


In [ ]:
# automating alzheimers dataset for KNN and Transformer

# extract files from folders
import os
folders = os.listdir(r"/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase")
folders.remove('.DS_Store')

# iterate through files
alzheimers_data = []
headers = []

for i in range(len(folders)):
    address = r"/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase" + "/" + folders[i]
    files = os.listdir(address)
    for j in range(len(files)):
        path = address + "/" + files[j]
        alzheimers_data.append(path)
        temp = folders[i] + "/" + files[j]
        headers.append(temp)

In [ ]:
# sort alzheiemrs data into train and test

alzheimers_data_train = [] # train is A and C
headers_train = []
alzheimers_data_test = [] # test is B and D
headers_test = []

# sorting alzheimers dataset into test and train

for i in range(len(headers)):
  if ('SETA' in headers[i]) or ('SETC' in headers[i]):
    alzheimers_data_train.append(alzheimers_data[i])
    headers_train.append(headers[i])
  else:
    alzheimers_data_test.append(alzheimers_data[i])
    headers_test.append(headers[i])

transfers = []

# move half of set D to train to make alzheimer's data 75-25 split


for i in range(6):
  if 'SETD' in alzheimers_data_test[i]:
    alzheimers_data_train.append(alzheimers_data_test[i])
    headers_train.append(headers_test[i])

del alzheimers_data_test[0:6]
del headers_test[0:6]

for i in range(6):
  if 'SETB' in alzheimers_data_test[i+6]:
    alzheimers_data_train.append(alzheimers_data_test[i+6])
    headers_train.append(headers_test[i+6])

del alzheimers_data_test[6:12]
del headers_test[6:12]

print(alzheimers_data_train)
print(alzheimers_data_test)

['/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0301.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0303.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0302.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0304.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0204.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0202.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0102.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0101.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0104.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0203.out', '/content/drive/MyDrive/EEG_project/alzheimers_EEG/DataBase/DataBase/SETC/eo0103.out', '/content/drive/MyDrive/EEG_project/alzhei

In [ ]:
# function to shuffle train and test in unison
def shuffle_in_unison(a, b):
    assert len(a) == len(b)
    shuffled_a = np.empty(a.shape, dtype=a.dtype)
    shuffled_b = np.empty(b.shape, dtype=b.dtype)
    permutation = np.random.permutation(len(a))
    for old_index, new_index in enumerate(permutation):
        shuffled_a[new_index] = a[old_index]
        shuffled_b[new_index] = b[old_index]
    return shuffled_a, shuffled_b

In [ ]:
import numpy

alzheimers_data_train = numpy.array(alzheimers_data_train)
alzheimers_data_test = numpy.array(alzheimers_data_test)
headers_train = numpy.array(headers_train)
headers_test = numpy.array(headers_test)

alzheimers_data_train, headers_train = shuffle_in_unison(alzheimers_data_train, headers_train)
alzheimers_data_test, headers_test = shuffle_in_unison(alzheimers_data_test, headers_test)

In [ ]:
device = "cuda" if torch.cuda.is_available() else "cpu"

model = model.to(device)

In [ ]:
# make inputs into transformer smaller
# ORIGINAL MODEL THAT BREAKS UP SEGMENTS
"""
model.train()

import re
from io import StringIO

num_epochs = 3
for epoch in tqdm(range(num_epochs)):

  # data preprocessing
  for i in range(len(alzheimers_data_train)):

      # open and read the files
      f = open(alzheimers_data_train[i],"r")
      s = f.read()

      # replace all spaces in the dataset with commas so it can be a list
      s = re.sub("\s+", ",", s.strip())
      TESTDATA = StringIO(s)
      s = pd.read_csv(TESTDATA, sep=",", header=None).values.tolist()[0]


      # channel 1 data is index 0, 19, 38, ... channel 2 data is index 1, 20, 39, 58, 77, ...
      temp = []
      for idx1 in range(19):
        t = []
        for idx2 in range(int(len(s)/19)):
          t.append(s[idx1+19*idx2])
        temp.append(t)

      # number of channels in a variable
      data = temp
      num_channels = len(data)

      # 0 is benign
      if 'SETA' in headers_train[i]:
        labels = torch.zeros(1)
      elif 'SETB' in headers_train[i]:
        labels = torch.zeros(1)
      else:
        labels = torch.ones(1)

      labels = labels.to(device)

      # break each channel into pieces of 512
      for channel in range(num_channels):
          temp1 = []
          attention_mask1 = []
          for part in range(int(len(data[channel])/512)):
              sample = []
              idx_i = 512*part
              idx_f = idx_i + 512
              temp = data[channel][idx_i:idx_f]
              for pad in range(256):
                temp.append(0)
              # normalize data
              temp = [temp]
              # temp = preprocessing.normalize(temp)
              # feed data inot KNN
              knn_output_IDs = classifier.predict(temp)
              # convert output of knn
              temp = [word_token_IDs[knn_output_IDs[0]]]
              # pad each list to length 512
              temp = torch.tensor(temp)
              temp = torch.nn.functional.pad(temp, (0,512-len(temp[0])))
              # create attention mask
              attention_mask = torch.gt(temp, 0).int()
              # feed IDs and attention masks into model
              temp1.append(temp)
              attention_mask1.append(attention_mask)

          temp1 = torch.stack(temp1)
          # temp1 = torch.tensor(temp1)

          attention_mask1 = torch.stack(attention_mask1)
          # attention_mask1 = torch.tensor(attention_mask1)

          temp1 = temp1.to(device)
          attention_mask1 = attention_mask1.to(device)

          transformer_input = {'input_ids': temp1.squeeze(), 'attention_mask': attention_mask1.squeeze()}

          if (int(len(data[channel])/512) == 2):
              labels1 = torch.stack([labels,labels])
          else:
              labels1 = torch.stack([labels,labels,labels])

          labels1 = labels1.squeeze(1)


          num_epochs1 = 1
          for epoch1 in range(num_epochs1):
            output = model(**transformer_input)
            output1 = torch.sigmoid(output.mean(1).squeeze(1))

            # optimization
            loss = torch.nn.functional.mse_loss(output1, labels1) # functional.binary_cross_entropy
            loss.backward()

          print("OUTPUT OF MODEL:")
          print(output1)
          print(labels1)

          optimizer.step()
          lr_scheduler.step()
          optimizer.zero_grad()

      # output of transformer
      print("successfully processed: " + headers_train[i])
      print(labels)
      """

'\nmodel.train()\n\nimport re\nfrom io import StringIO\n\nnum_epochs = 3\nfor epoch in tqdm(range(num_epochs)):\n\n  # data preprocessing\n  for i in range(len(alzheimers_data_train)):\n\n      # open and read the files\n      f = open(alzheimers_data_train[i],"r")\n      s = f.read()\n\n      # replace all spaces in the dataset with commas so it can be a list\n      s = re.sub("\\s+", ",", s.strip())\n      TESTDATA = StringIO(s)\n      s = pd.read_csv(TESTDATA, sep=",", header=None).values.tolist()[0]\n\n\n      # channel 1 data is index 0, 19, 38, ... channel 2 data is index 1, 20, 39, 58, 77, ...\n      temp = []\n      for idx1 in range(19):\n        t = []\n        for idx2 in range(int(len(s)/19)):\n          t.append(s[idx1+19*idx2])\n        temp.append(t)\n\n      # number of channels in a variable\n      data = temp\n      num_channels = len(data)\n\n      # 0 is benign\n      if \'SETA\' in headers_train[i]:\n        labels = torch.zeros(1)\n      elif \'SETB\' in headers_t

In [ ]:
# make inputs into transformer smaller

model.train()

import re
from io import StringIO

num_epochs = 1
for epoch in tqdm(range(num_epochs)):

  # data preprocessing
  for i in range(len(alzheimers_data_train)):

      # open and read the files
      f = open(alzheimers_data_train[i],"r")
      s = f.read()

      # replace all spaces in the dataset with commas so it can be a list
      s = re.sub("\s+", ",", s.strip())
      TESTDATA = StringIO(s)
      s = pd.read_csv(TESTDATA, sep=",", header=None).values.tolist()[0]


      # channel 1 data is index 0, 19, 38, ... channel 2 data is index 1, 20, 39, 58, 77, ...
      temp = []
      for idx1 in range(19):
        t = []
        for idx2 in range(int(len(s)/19)):
          t.append(s[idx1+19*idx2])
        temp.append(t)

      # number of channels in a variable
      data = temp
      num_channels = len(data)

      # 0 is benign
      if 'SETA' in headers_train[i]:
        labels = torch.zeros(1)
      elif 'SETB' in headers_train[i]:
        labels = torch.zeros(1)
      else:
        labels = torch.ones(1)

      labels = labels.to(device)

      # break each channel into pieces of 512
      for channel in range(num_channels):
          temp1 = []
          attention_mask1 = []
          channel_knn = []
          for part in range(int(len(data[channel])/512)):
              sample = []
              idx_i = 512*part
              idx_f = idx_i + 512
              temp = data[channel][idx_i:idx_f]
              temp = preprocessing.normalize([temp])

              temp = torch.tensor(temp)
              temp = temp.repeat(768, 1)
              temp = temp.T
              temp = torch.unsqueeze(temp,0)

              temp = temp.float().to('cuda')
              output = model(temp)
              output1 = torch.sigmoid(output.mean(1))

              # optimization
              loss = torch.nn.functional.binary_cross_entropy(output1[0], labels) # functional.binary_cross_entropy
              loss.backward()

              print("OUTPUT OF MODEL:")
              print(output1[0])
              print(labels)

              optimizer.step()
              lr_scheduler.step()
              optimizer.zero_grad()

    # output of transformer
      print("successfully processed: " + headers_train[i])
      print(labels)


  0%|          | 0/1 [00:00<?, ?it/s]

Streaming output truncated to the last 5000 lines.
OUTPUT OF MODEL:
tensor([0.3634], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.3497], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.3879], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.3613], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.5062], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.3932], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF MODEL:
tensor([0.4370], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([0.], device='cuda:0')
torch.Size([1, 512, 768])
OUTPUT OF M

100%|██████████| 1/1 [00:51<00:00, 51.65s/it]

OUTPUT OF MODEL:
tensor([0.3708], device='cuda:0', grad_fn=<SelectBackward0>)
tensor([1.], device='cuda:0')
successfully processed: SETC/eo0301.out
tensor([1.], device='cuda:0')


In [ ]:
import joblib
import pickle

filename = "/content/drive/MyDrive/EEG_project/Code/DistilBERT/DistilBERT.joblib"
joblib.dump(model, filename)
# model = joblib.load(filename)

In [ ]:
Y_test = []
Y_preds = []

In [ ]:
model.eval()

import re
from io import StringIO

num_epochs = 1
for epoch in tqdm(range(num_epochs)):

  # data preprocessing
  for i in range(len(alzheimers_data_test)):#####

      # open and read the files
      f = open(alzheimers_data_test[i],"r")#####
      s = f.read()

      # replace all spaces in the dataset with commas so it can be a list
      s = re.sub("\s+", ",", s.strip())
      TESTDATA = StringIO(s)
      s = pd.read_csv(TESTDATA, sep=",", header=None).values.tolist()[0]


      # channel 1 data is index 0, 19, 38, ... channel 2 data is index 1, 20, 39, 58, 77, ...
      temp = []
      for idx1 in range(19):
        t = []
        for idx2 in range(int(len(s)/19)):
          t.append(s[idx1+19*idx2])
        temp.append(t)

      # number of channels in a variable
      data = temp
      num_channels = len(data)



      with torch.no_grad():
        for channel in range(num_channels):

          for part in range(int(len(data[channel])/512)):
              sample = []
              idx_i = 512*part
              idx_f = idx_i + 512
              temp = data[channel][idx_i:idx_f]

              temp = preprocessing.normalize([temp])

              temp = torch.tensor(temp)
              temp = temp.repeat(768, 1)
              temp = temp.T
              temp = torch.unsqueeze(temp,0)

              temp = temp.float().to('cuda')
              output = model(temp)
              output1 = torch.sigmoid(output.mean(1))

              Y_preds.append(output1[0])
              Y_test.append(labels)

    # output of transformer
      print("successfully processed: " + headers_test[i])#####
      print(labels)


  0%|          | 0/1 [00:00<?, ?it/s]

successfully processed: SETD/ec0304.out
tensor([1.], device='cuda:0')
successfully processed: SETD/ec0103.out
tensor([1.], device='cuda:0')
successfully processed: SETB/eeg24c1.out
tensor([1.], device='cuda:0')
successfully processed: SETB/eeg20c1.out
tensor([1.], device='cuda:0')
successfully processed: SETB/eeg23c1.out
tensor([1.], device='cuda:0')
successfully processed: SETD/ec0102.out
tensor([1.], device='cuda:0')
successfully processed: SETB/eeg21c1.out
tensor([1.], device='cuda:0')
successfully processed: SETD/ec0101.out
tensor([1.], device='cuda:0')
successfully processed: SETB/eeg27c1.out
tensor([1.], device='cuda:0')
successfully processed: SETD/ec0104.out
tensor([1.], device='cuda:0')
successfully processed: SETD/ec0201.out
tensor([1.], device='cuda:0')


100%|██████████| 1/1 [00:16<00:00, 16.11s/it]

successfully processed: SETB/eeg22c1.out
tensor([1.], device='cuda:0')


In [ ]:
# make inputs into transformer smaller
# ACTUAL CODE
"""
model.eval()

import re
from io import StringIO

# data preprocessing
for i in tqdm(range(len(alzheimers_data_test))):

    # open and read the files
    f = open(alzheimers_data_test[i],"r")
    s = f.read()

    # replace all spaces in the dataset with commas so it can be a list
    s = re.sub("\s+", ",", s.strip())
    TESTDATA = StringIO(s)
    s = pd.read_csv(TESTDATA, sep=",", header=None).values.tolist()[0]


    # channel 1 data is index 0, 19, 38, ... channel 2 data is index 1, 20, 39, 58, 77, ...
    temp = []
    for idx1 in range(19):
      t = []
      for idx2 in range(int(len(s)/19)):
        t.append(s[idx1+19*idx2])
      temp.append(t)

    # number of channels in a variable
    data = temp
    num_channels = len(data)

    # 0 is benign
    if 'SETA' in headers_test[i]:
      labels = torch.zeros(1)
    elif 'SETB' in headers_test[i]:
      labels = torch.zeros(1)
    else:
      labels = torch.ones(1)

    labels = labels.to(device)


    # break each channel into pieces of 512
    with torch.no_grad():
      for channel in range(num_channels):
          for part in range(int(len(data[channel])/512)):
              sample = []
              idx_i = 512*part
              idx_f = idx_i + 512
              temp = data[channel][idx_i:idx_f]
              for pad in range(256):
                temp.append(0)
              # normalize data
              temp = [temp]
              # temp = preprocessing.normalize(temp)
              # feed data inot KNN
              knn_output_IDs = classifier.predict(temp)
              # convert output of knn
              temp = [word_token_IDs[knn_output_IDs[0]]]
              # pad each list to length 512
              temp = torch.tensor(temp)
              temp = torch.nn.functional.pad(temp, (0,512-len(temp[0])))
              # create attention mask
              attention_mask = torch.gt(temp, 0).int()
              # feed IDs and attention masks into model
              temp = temp.to(device)
              attention_mask = attention_mask.to(device)
              transformer_input = {'input_ids': temp, 'attention_mask': attention_mask}
              output = model(**transformer_input)
              output = torch.sigmoid(output.mean(1).squeeze(1))

              Y_preds.append(output)
              Y_test.append(labels)

      # output of transformer
      print("successfully processed: " + headers_test[i])
      print(labels)
"""

In [ ]:
temp1 = []

for i in range(len(Y_preds)):
  temp1.append(Y_preds[i].item())

Y_preds_original = Y_preds
Y_preds = temp1


In [ ]:
temp1 = []

for i in range(len(Y_test)):
  temp1.append(Y_test[i].item())

Y_test_original = Y_test
Y_test = temp1